## Validation of data

### 1. assignments table

In [2]:
SELECT *
FROM INFORMATION_SCHEMA.COLUMNS
WHERE table_name = 'assignments'

table_catalog table_schema  ... generation_expression is_updatable
0      projects       public  ...                   NaN          YES
1      projects       public  ...                   NaN          YES
2      projects       public  ...                   NaN          YES
3      projects       public  ...                   NaN          YES
4      projects       public  ...                   NaN          YES
5      projects       public  ...                   NaN          YES
6      projects       public  ...                   NaN          YES

[7 rows x 44 columns]

In [3]:
SELECT *
FROM assignments;

assignment_id  assignment_name start_date  ...    budget  region impact_score
0                 1     Assignment_1 2021-10-17  ... -32322.03    West         5.55
1                 2     Assignment_2 2020-10-26  ...  57278.40   South         1.45
2                 3     Assignment_3 2021-08-11  ...  40414.51    West         2.34
3                 4     Assignment_4 2021-11-22  ...  31732.48    East         7.05
4                 5     Assignment_5 2020-11-22  ...  13548.22   North         5.29
...             ...              ...        ...  ...       ...     ...          ...
4995           4996  Assignment_4996 2021-06-04  ... -17276.64    West         5.85
4996           4997  Assignment_4997 2021-01-26  ... -14681.98   South         4.68
4997           4998  Assignment_4998 2021-03-10  ... -20391.76    West         3.46
4998           4999  Assignment_4999 2021-12-10  ...   9803.08   South         9.55
4999           5000  Assignment_5000 2020-12-10  ...  93788.97    West         3.79

[5000 rows x 7 columns]

In [9]:
-- assignment_name column
SELECT assignment_name, COUNT(*) AS total
FROM assignments
GROUP BY assignment_name
ORDER BY total DESC;

assignment_name  total
0      Assignment_184      1
1     Assignment_2638      1
2      Assignment_733      1
3     Assignment_4685      1
4     Assignment_3763      1
...               ...    ...
4995  Assignment_1507      1
4996  Assignment_3286      1
4997  Assignment_2861      1
4998  Assignment_3647      1
4999  Assignment_1683      1

[5000 rows x 2 columns]

In [10]:
-- region column
SELECT region, COUNT(*) AS total
FROM assignments
GROUP BY region 
ORDER BY total DESC;

region  total
0  South   1276
1   West   1254
2   East   1246
3  North   1224

In [6]:
-- budget column
SELECT COUNT(*) AS total,
	COUNT(budget) AS no_null,
	MIN(budget),
	MAX(budget),
	AVG(budget),
	PERCENTILE_CONT(0.5) WITHIN GROUP (ORDER BY budget) AS median
FROM assignments;

total  no_null       min      max           avg    median
0   5000     5000 -99235.29  99994.6  24210.295808  23438.66

In [14]:
SELECT COUNT(*) AS budget_negative
FROM assignments
WHERE budget < 0;

budget_negative
0             1730

In [7]:
-- impact_score column
SELECT COUNT(*) AS total,
	COUNT(impact_score) AS no_null,
	MIN(impact_score),
	MAX(impact_score),
	AVG(impact_score),
	PERCENTILE_CONT(0.5) WITHIN GROUP (ORDER BY impact_score) AS median
FROM assignments;	

total  no_null  min   max       avg  median
0   5000     5000  1.0  10.0  5.440372    5.39

In [19]:
-- assignment_id column
SELECT COUNT(*) AS total,
	COUNT(assignment_id) AS no_null,
	MIN(assignment_id),
	MAX(assignment_id),
	AVG(assignment_id),
	PERCENTILE_CONT(0.5) WITHIN GROUP (ORDER BY assignment_id) AS median
FROM assignments;	

total  no_null  min   max     avg  median
0   5000     5000    1  5000  2500.5  2500.5

In [15]:
-- start_date column
SELECT DISTINCT
	CASE WHEN start_date::VARCHAR LIKE '%T%' THEN 'ISO 8601'
	WHEN start_date::VARCHAR ~ '^\d{2}/\d{2}/\d{4}$' THEN 'DD/MM/YYYY'
	WHEN start_date::VARCHAR ~ '^\d{4}-\d{2}-\d{2}$' THEN 'YYYY-MM-DD'
	ELSE 'Other format' END AS format,
	COUNT(*) AS rows_n
FROM assignments
GROUP BY format;

format  rows_n
0    DD/MM/YYYY    1694
1  Other format    1637
2    YYYY-MM-DD    1669

In [17]:
-- Verifying Other format
SELECT
    start_date,
    SPLIT_PART(TRIM(start_date::VARCHAR), '-', 3) AS start_date_year,
    SPLIT_PART(TRIM(start_date::VARCHAR), '-', 1) AS start_date_month,
    SPLIT_PART(TRIM(start_date::VARCHAR), '-', 2) AS start_date_day,
    TO_DATE(
        SPLIT_PART(TRIM(start_date::VARCHAR), '-', 3) || '-' || 
        LPAD(SPLIT_PART(TRIM(start_date::VARCHAR), '-', 1), 2, '0') || '-' || 
        LPAD(SPLIT_PART(TRIM(start_date::VARCHAR), '-', 2), 2, '0'),
        'YYYY-MM-DD') AS start_date_cleaned
FROM assignments
WHERE start_date NOT LIKE '%T%' 
  AND start_date !~ '^\d{2}/\d{2}/\d{4}$' 
  AND start_date !~ '^\d{4}-\d{2}-\d{2}$';

start_date  start_date_year  ...  start_date_day        start_date_cleaned
0    2021-08-11             2021  ...              11 2021-08-11 00:00:00+00:00
1    2020-11-22             2020  ...              22 2020-11-22 00:00:00+00:00
2    2020-07-20             2020  ...              20 2020-07-20 00:00:00+00:00
3    2021-12-14             2021  ...              14 2021-12-14 00:00:00+00:00
4    2020-08-23             2020  ...              23 2020-08-23 00:00:00+00:00
...         ...              ...  ...             ...                       ...
1632 2021-06-23             2021  ...              23 2021-06-23 00:00:00+00:00
1633 2020-06-11             2020  ...              11 2020-06-11 00:00:00+00:00
1634 2021-07-15             2021  ...              15 2021-07-15 00:00:00+00:00
1635 2020-06-27             2020  ...              27 2020-06-27 00:00:00+00:00
1636 2021-03-10             2021  ...              10 2021-03-10 00:00:00+00:00

[1637 rows x 5 columns]

In [18]:
-- Final cleaning of start_date column
SELECT 
    start_date,
    CASE
        -- Case 1: DD/MM/YYYY
        WHEN TRIM(start_date::VARCHAR) ~ '^\d{2}/\d{2}/\d{4}$'
            THEN TO_DATE(TRIM(start_date), 'DD/MM/YYYY')
        -- Caso 2: YYYY-MM-DD
        WHEN TRIM(start_date::VARCHAR) ~ '^\d{4}-\d{2}-\d{2}$'
            THEN TO_DATE(TRIM(start_date), 'YYYY-MM-DD')
        -- Caso 3: Other format
        ELSE TO_DATE(
        SPLIT_PART(TRIM(start_date::VARCHAR), '-', 3) || '-' || 
        LPAD(SPLIT_PART(TRIM(start_date::VARCHAR), '-', 1), 2, '0') || '-' || 
        LPAD(SPLIT_PART(TRIM(start_date::VARCHAR), '-', 2), 2, '0'),
        'YYYY-MM-DD') END AS start_date_cleaned
FROM assignments;

start_date        start_date_cleaned
0    2021-10-17 2021-10-17 00:00:00+00:00
1    2020-10-26 2020-10-26 00:00:00+00:00
2    2021-08-11 2021-08-11 00:00:00+00:00
3    2021-11-22 2021-11-22 00:00:00+00:00
4    2020-11-22 2020-11-22 00:00:00+00:00
...         ...                       ...
4995 2021-06-04 2021-04-06 00:00:00+00:00
4996 2021-01-26 2021-01-26 00:00:00+00:00
4997 2021-03-10 2021-03-10 00:00:00+00:00
4998 2021-12-10 2021-10-12 00:00:00+00:00
4999 2020-12-10 2020-10-12 00:00:00+00:00

[5000 rows x 2 columns]

In [19]:
-- end_date column
SELECT DISTINCT
	CASE WHEN end_date::VARCHAR LIKE '%T%' THEN 'ISO 8601'
	WHEN end_date::VARCHAR ~ '^\d{2}/\d{2}/\d{4}$' THEN 'DD/MM/YYYY'
	WHEN end_date::VARCHAR ~ '^\d{4}-\d{2}-\d{2}$' THEN 'YYYY-MM-DD'
	ELSE 'Other format' END AS format,
	COUNT(*) AS rows_n
FROM assignments
GROUP BY format;

format  rows_n
0    YYYY-MM-DD    1639
1    DD/MM/YYYY    1660
2  Other format    1701

In [24]:
-- Verifying Other format
SELECT
    end_date,
    SPLIT_PART(TRIM(end_date::VARCHAR), '-', 3) AS end_date_year,
    SPLIT_PART(TRIM(end_date::VARCHAR), '-', 1) AS end_date_month,
    SPLIT_PART(TRIM(end_date::VARCHAR), '-', 2) AS end_date_day,
    TO_DATE(
        SPLIT_PART(TRIM(end_date::VARCHAR), '-', 3) || '-' || 
        LPAD(SPLIT_PART(TRIM(end_date::VARCHAR), '-', 1), 2, '0') || '-' || 
        LPAD(SPLIT_PART(TRIM(end_date::VARCHAR), '-', 2), 2, '0'),
        'YYYY-MM-DD') AS end_date_cleaned
FROM assignments
WHERE end_date NOT LIKE '%T%' 
  AND end_date !~ '^\d{2}/\d{2}/\d{4}$' 
  AND end_date !~ '^\d{4}-\d{2}-\d{2}$';

end_date  end_date_year  ...  end_date_day          end_date_cleaned
0    2020-11-28           2020  ...            28 2020-11-28 00:00:00+00:00
1    2022-05-17           2022  ...            17 2022-05-17 00:00:00+00:00
2    2020-11-18           2020  ...            18 2020-11-18 00:00:00+00:00
3    2021-03-10           2021  ...            10 2021-03-10 00:00:00+00:00
4    2022-05-11           2022  ...            11 2022-05-11 00:00:00+00:00
...         ...            ...  ...           ...                       ...
1696 2021-05-28           2021  ...            28 2021-05-28 00:00:00+00:00
1697 2022-03-14           2022  ...            14 2022-03-14 00:00:00+00:00
1698 2020-10-26           2020  ...            26 2020-10-26 00:00:00+00:00
1699 2021-04-13           2021  ...            13 2021-04-13 00:00:00+00:00
1700 2022-02-15           2022  ...            15 2022-02-15 00:00:00+00:00

[1701 rows x 5 columns]

In [26]:
-- Final cleaning of end_date column
SELECT 
    end_date,
    CASE
        -- Case 1: DD/MM/YYYY
        WHEN TRIM(end_date::VARCHAR) ~ '^\d{2}/\d{2}/\d{4}$'
            THEN TO_DATE(TRIM(end_date), 'DD/MM/YYYY')
        -- Caso 2: YYYY-MM-DD
        WHEN TRIM(end_date::VARCHAR) ~ '^\d{4}-\d{2}-\d{2}$'
            THEN TO_DATE(TRIM(end_date), 'YYYY-MM-DD')
        -- Caso 3: Other format
        ELSE TO_DATE(
        SPLIT_PART(TRIM(end_date::VARCHAR), '-', 3) || '-' || 
        LPAD(SPLIT_PART(TRIM(end_date::VARCHAR), '-', 1), 2, '0') || '-' || 
        LPAD(SPLIT_PART(TRIM(end_date::VARCHAR), '-', 2), 2, '0'),
        'YYYY-MM-DD') END AS end_date_cleaned
FROM assignments;

end_date          end_date_cleaned
0    2021-12-04 2021-12-04 00:00:00+00:00
1    2020-11-28 2020-11-28 00:00:00+00:00
2    2022-03-17 2022-03-17 00:00:00+00:00
3    2022-05-17 2022-05-17 00:00:00+00:00
4    2021-07-10 2021-10-07 00:00:00+00:00
...         ...                       ...
4995 2022-02-15 2022-02-15 00:00:00+00:00
4996 2021-08-03 2021-08-03 00:00:00+00:00
4997 2021-12-05 2021-05-12 00:00:00+00:00
4998 2022-07-22 2022-07-22 00:00:00+00:00
4999 2021-04-10 2021-04-10 00:00:00+00:00

[5000 rows x 2 columns]

## 2. donations table

In [17]:
SELECT *
FROM INFORMATION_SCHEMA.COLUMNS
WHERE table_name = 'donations';

table_catalog table_schema  ... generation_expression is_updatable
0      projects       public  ...                   NaN          YES
1      projects       public  ...                   NaN          YES
2      projects       public  ...                   NaN          YES
3      projects       public  ...                   NaN          YES
4      projects       public  ...                   NaN          YES

[5 rows x 44 columns]

In [18]:
SELECT *
FROM donations;

donation_id  donor_id  amount             donation_date  assignment_id
0               1      2733  271.36 2021-08-21 00:00:00+00:00           4226
1               2      2608  251.49 2021-10-15 00:00:00+00:00           1323
2               3      1654  528.38 2020-03-03 00:00:00+00:00           4881
3               4      3265  730.36 2021-02-06 00:00:00+00:00           1237
4               5      4932  285.96 2022-03-05 00:00:00+00:00           1626
...           ...       ...     ...                       ...            ...
4995         4996      4770  798.63 2020-03-08 00:00:00+00:00           4012
4996         4997      4093  693.00 2022-04-10 00:00:00+00:00           4700
4997         4998      2569   57.04 2021-11-04 00:00:00+00:00           2688
4998         4999       847   41.62 2022-11-29 00:00:00+00:00           1053
4999         5000      2538  454.82 2020-06-19 00:00:00+00:00           2882

[5000 rows x 5 columns]

In [20]:
-- donation_id column
SELECT COUNT(*) AS total,
	COUNT(donation_id) AS no_null,
	MIN(donation_id),
	MAX(donation_id),
	AVG(donation_id),
	PERCENTILE_CONT(0.5) WITHIN GROUP (ORDER BY donation_id) AS median
FROM donations;	

total  no_null  min   max     avg  median
0   5000     5000    1  5000  2500.5  2500.5

In [22]:
-- donor_id column
SELECT COUNT(*) AS total,
	COUNT(donor_id) AS no_null,
	MIN(donor_id),
	MAX(donor_id),
	AVG(donor_id),
	PERCENTILE_CONT(0.5) WITHIN GROUP (ORDER BY donor_id) AS median
FROM donations;	

total  no_null  min   max        avg  median
0   5000     5000    1  5000  2481.9536    2472

In [23]:
-- amount column
SELECT COUNT(*) AS total,
	COUNT(amount) AS no_null,
	MIN(amount),
	MAX(amount),
	AVG(amount),
	PERCENTILE_CONT(0.5) WITHIN GROUP (ORDER BY amount) AS median
FROM donations;	

total  no_null    min    max         avg  median
0   5000     5000  10.02  999.9  505.315858  506.93

In [24]:
-- assignment_id column
SELECT COUNT(*) AS total,
	COUNT(assignment_id) AS no_null,
	MIN(assignment_id),
	MAX(assignment_id),
	AVG(assignment_id),
	PERCENTILE_CONT(0.5) WITHIN GROUP (ORDER BY assignment_id) AS median
FROM donations;	

total  no_null  min   max        avg  median
0   5000     5000    1  5000  2506.1958    2516

In [27]:
-- donation_date column
SELECT DISTINCT
	CASE WHEN donation_date::VARCHAR LIKE '%T%' THEN 'ISO 8601'
	WHEN donation_date::VARCHAR ~ '^\d{2}/\d{2}/\d{4}$' THEN 'DD/MM/YYYY'
	WHEN donation_date::VARCHAR ~ '^\d{4}-\d{2}-\d{2}$' THEN 'YYYY-MM-DD'
	ELSE 'Other format' END AS format,
	COUNT(*) AS rows_n
FROM donations
GROUP BY format;

format  rows_n
0  YYYY-MM-DD    5000

## 3. donors table

In [25]:
SELECT *
FROM INFORMATION_SCHEMA.COLUMNS
WHERE table_name = 'donors';	

table_catalog table_schema  ... generation_expression is_updatable
0      projects       public  ...                   NaN          YES
1      projects       public  ...                   NaN          YES
2      projects       public  ...                   NaN          YES

[3 rows x 44 columns]

In [30]:
SELECT *
FROM donors;

donor_id  donor_name    donor_type
0            1     Donor_1    Individual
1            2     Donor_2  Organization
2            3     Donor_3    Individual
3            4     Donor_4  Organization
4            5     Donor_5  Organization
...        ...         ...           ...
4995      4996  Donor_4996    Individual
4996      4997  Donor_4997     Corporate
4997      4998  Donor_4998    Individual
4998      4999  Donor_4999    Individual
4999      5000  Donor_5000  Organization

[5000 rows x 3 columns]

In [26]:
-- donor_id column
SELECT COUNT(*) AS total,
	COUNT(donor_id) AS no_null,
	MIN(donor_id),
	MAX(donor_id),
	AVG(donor_id),
	PERCENTILE_CONT(0.5) WITHIN GROUP (ORDER BY donor_id) AS median
FROM donors;	

total  no_null  min   max     avg  median
0   5000     5000    1  5000  2500.5  2500.5

In [28]:
-- donor_name column
SELECT donor_name, COUNT(*) AS total
FROM donors
GROUP BY donor_name 
ORDER BY total DESC;

donor_name  total
0     Donor_3870      1
1     Donor_3598      1
2      Donor_319      1
3     Donor_2078      1
4     Donor_3645      1
...          ...    ...
4995   Donor_841      1
4996   Donor_582      1
4997  Donor_4448      1
4998  Donor_4191      1
4999  Donor_3222      1

[5000 rows x 2 columns]

In [29]:
-- donor_type column
SELECT donor_type, COUNT(*) AS total
FROM donors
GROUP BY donor_type 
ORDER BY total DESC;

donor_type  total
0  Organization   1682
1    Individual   1672
2     Corporate   1646

## Analysis

#### Who are the top five assignments based on total value of donations, categorized by donor type? 

In [31]:
-- highest_donation_assignments
SELECT a.assignment_name, 
	a.region, 
	ROUND(SUM(d.amount),2) AS rounded_total_donation_amount, 
	dn.donor_type
FROM donations AS d
INNER JOIN assignments AS a
	ON d.assignment_id = a.assignment_id
INNER JOIN donors AS dn
	ON d.donor_id = dn.donor_id
GROUP BY 
	a.assignment_name,
	a.region,
	dn.donor_type
ORDER BY rounded_total_donation_amount DESC
LIMIT 5;

assignment_name region  rounded_total_donation_amount    donor_type
0  Assignment_3033   East                        3840.66    Individual
1   Assignment_300   West                        3133.98  Organization
2  Assignment_4114  North                        2778.57  Organization
3  Assignment_1765   West                        2626.98  Organization
4   Assignment_268   East                        2488.69    Individual

#### Identify the assignment with the highest impact score in each region, ensuring that each listed assignment has received at least one donation

In [32]:
-- top_regional_impact_assignments
WITH donation_counts AS(
	SELECT 
		assignment_id,
		COUNT(*) AS num_total_donations
	FROM donations
	GROUP BY assignment_id),

ranked_assignments AS(
	SELECT 
		a.assignment_name,
		a.region, 
		a.impact_score,
		d.num_total_donations,
		ROW_NUMBER() OVER(PARTITION BY a.region ORDER BY a.impact_score DESC) AS row_numb
	FROM assignments AS a
	INNER JOIN donation_counts AS d
		ON a.assignment_id = d.assignment_id)

SELECT
assignment_name,
region,
impact_score,
num_total_donations
FROM ranked_assignments
WHERE row_numb = 1
ORDER BY region;

assignment_name region  impact_score  num_total_donations
0   Assignment_316   East         10.00                    2
1  Assignment_2253  North          9.99                    1
2  Assignment_3547  South         10.00                    1
3  Assignment_2794   West          9.99                    2

### Which is donation trend over time?

In [5]:
SELECT
	EXTRACT(YEAR FROM donation_date) AS year_donation,
	ROUND(SUM(amount), 2)
FROM donations
GROUP BY year_donation
ORDER BY year_donation;

year_donation      round
0           2020  866914.68
1           2021  819859.27
2           2022  839805.34

Although donations picked up in 2020 at nearly $867K, the following year saw a decline. In 2022, donations increased compared to 2021, but they still fell short of 2020 levels. This highlights the need to reinforce donor engagement strategies to return to peak levels.

### Which regions have received the most founding compared with their impact?

In [9]:
SELECT
	a.region,
	SUM(d.amount) AS total_donation,
	ROUND(AVG(a.impact_score),2) AS avg_impact_score
FROM assignments AS a
INNER JOIN donations AS d
USING(assignment_id)
GROUP BY a.region
ORDER BY total_donation DESC;

region  total_donation  avg_impact_score
0  South       644650.20              5.54
1   East       638713.17              5.44
2   West       632296.84              5.45
3  North       610919.08              5.42

Across the regions, donations remain relatively balanced, with each exceeding $600K. However, the South attracts the highest funding and has the strongest average impact (5.54).

### Types of remarkable donors

In [14]:
SELECT
	don.donor_type,
	ROUND(SUM(d.amount),2) AS total_donations,
	ROUND(SUM(d.amount)*100/SUM(SUM(d.amount)) OVER(),2) AS percentaje_impact
FROM donors AS don
INNER JOIN donations AS d
USING(donor_id)
GROUP BY don.donor_type
ORDER BY total_donations DESC;

donor_type  total_donations  percentaje_impact
0  Organization        860175.04              34.05
1    Individual        840073.79              33.25
2     Corporate        826330.46              32.71

### Projects duration vs impact achieve

In [16]:
WITH startdate AS(
	SELECT
		assignment_id,
    	CASE
        	WHEN TRIM(start_date::VARCHAR) ~ '^\d{2}/\d{2}/\d{4}$'
				THEN TO_DATE(TRIM(start_date), 'DD/MM/YYYY')
        	WHEN TRIM(start_date::VARCHAR) ~ '^\d{4}-\d{2}-\d{2}$'
            	THEN TO_DATE(TRIM(start_date), 'YYYY-MM-DD')
        	ELSE TO_DATE(
        	SPLIT_PART(TRIM(start_date::VARCHAR), '-', 3) || '-' || 
        	LPAD(SPLIT_PART(TRIM(start_date::VARCHAR), '-', 1), 2, '0') || '-' || 
        	LPAD(SPLIT_PART(TRIM(start_date::VARCHAR), '-', 2), 2, '0'),
        	'YYYY-MM-DD') END AS start_date_cleaned
	FROM assignments),
enddate AS(
	SELECT
		assignment_id,
    	CASE
        	WHEN TRIM(end_date::VARCHAR) ~ '^\d{2}/\d{2}/\d{4}$'
            	THEN TO_DATE(TRIM(end_date), 'DD/MM/YYYY')
        	WHEN TRIM(end_date::VARCHAR) ~ '^\d{4}-\d{2}-\d{2}$'
            	THEN TO_DATE(TRIM(end_date), 'YYYY-MM-DD')
        	ELSE TO_DATE(
        	SPLIT_PART(TRIM(end_date::VARCHAR), '-', 3) || '-' || 
        	LPAD(SPLIT_PART(TRIM(end_date::VARCHAR), '-', 1), 2, '0') || '-' || 
        	LPAD(SPLIT_PART(TRIM(end_date::VARCHAR), '-', 2), 2, '0'),
        	'YYYY-MM-DD') END AS end_date_cleaned
	FROM assignments)

SELECT
	a.assignment_name,
	a.region,
	(ed.end_date_cleaned - st.start_date_cleaned) AS duration_days,
	a.impact_score
FROM assignments AS a
INNER JOIN startdate AS st
	USING(assignment_id)
INNER JOIN enddate AS ed
	USING(assignment_id)
ORDER BY a.impact_score DESC;

assignment_name region  duration_days  impact_score
0      Assignment_316   East            309         10.00
1     Assignment_3547  South            277         10.00
2      Assignment_664  South             80         10.00
3     Assignment_1514   East            120          9.99
4     Assignment_2253  North            224          9.99
...               ...    ...            ...           ...
4995   Assignment_408   East            276          1.00
4996   Assignment_149  South            320          1.00
4997  Assignment_3138   East            184          1.00
4998  Assignment_4955   East            351          1.00
4999  Assignment_1124  North            300          1.00

[5000 rows x 4 columns]

In [19]:
WITH startdate AS(
	SELECT
		assignment_id,
    	CASE
        	WHEN TRIM(start_date::VARCHAR) ~ '^\d{2}/\d{2}/\d{4}$'
				THEN TO_DATE(TRIM(start_date), 'DD/MM/YYYY')
        	WHEN TRIM(start_date::VARCHAR) ~ '^\d{4}-\d{2}-\d{2}$'
            	THEN TO_DATE(TRIM(start_date), 'YYYY-MM-DD')
        	ELSE TO_DATE(
        	SPLIT_PART(TRIM(start_date::VARCHAR), '-', 3) || '-' || 
        	LPAD(SPLIT_PART(TRIM(start_date::VARCHAR), '-', 1), 2, '0') || '-' || 
        	LPAD(SPLIT_PART(TRIM(start_date::VARCHAR), '-', 2), 2, '0'),
        	'YYYY-MM-DD') END AS start_date_cleaned
	FROM assignments),
enddate AS(
	SELECT
		assignment_id,
    	CASE
        	WHEN TRIM(end_date::VARCHAR) ~ '^\d{2}/\d{2}/\d{4}$'
            	THEN TO_DATE(TRIM(end_date), 'DD/MM/YYYY')
        	WHEN TRIM(end_date::VARCHAR) ~ '^\d{4}-\d{2}-\d{2}$'
            	THEN TO_DATE(TRIM(end_date), 'YYYY-MM-DD')
        	ELSE TO_DATE(
        	SPLIT_PART(TRIM(end_date::VARCHAR), '-', 3) || '-' || 
        	LPAD(SPLIT_PART(TRIM(end_date::VARCHAR), '-', 1), 2, '0') || '-' || 
        	LPAD(SPLIT_PART(TRIM(end_date::VARCHAR), '-', 2), 2, '0'),
        	'YYYY-MM-DD') END AS end_date_cleaned
	FROM assignments)

SELECT
	CASE 
		WHEN a.impact_score BETWEEN 1 AND 3 THEN '1-3 Low impact'
		WHEN a.impact_score BETWEEN 4 AND 6 THEN '4-6 Medium impact'
		WHEN a.impact_score BETWEEN 7 AND 8 THEN '7-8 High impact'
		WHEN a.impact_score BETWEEN 9 AND 10 THEN '9-10 Very high impact'
		ELSE 'Not classified' END AS impact_score_range,
	ROUND(AVG(ed.end_date_cleaned - st.start_date_cleaned)) AS duration_days
FROM assignments AS a
INNER JOIN startdate AS st
	USING(assignment_id)
INNER JOIN enddate AS ed
	USING(assignment_id)
GROUP BY impact_score_range
ORDER BY duration_days DESC;

impact_score_range  duration_days
0         Not classified            201
1      4-6 Medium impact            196
2         1-3 Low impact            194
3  9-10 Very high impact            194
4        7-8 High impact            191

Project duration across impact levels is fairly unifor, suggesting that longer timelines do not automatically translate into higher impact. And very high impact projects are slightly shorter in duration, implying that effective planification and execution are key drivers of success.

### What proportion of projects have negative budget and how it has an effect in their impact?

In [21]:
SELECT
	CASE WHEN budget < 0 THEN 'Negative budget'
		ELSE 'Positive budget' END AS budget_type,
	COUNT(*) AS number_project,
	ROUND(AVG(impact_score),2) AS avg_impact_score
FROM assignments
GROUP BY budget_type;

budget_type  number_project  avg_impact_score
0  Positive budget            3270              5.41
1  Negative budget            1730              5.51

1730 projects have a negative budget; their average impact is slightly higher than that of projects executed with a positive budget. This suggests that having a negative budget doesn't necessarily reduce impact. It is important to explore the characteristics of these projects to generate better conclusions.